This tutorial walks through the process of using Snowflake Data Clean Rooms with Snowpark Container Services (SPCS). This is the provider notebook for this tutorial; be sure you also upload the consumer notebook to another Snowflake account with the clean rooms API installed.

**Prerequisites for SPCS**

- Make sure you have Docker installed and ready for building images.

**Prerequisites for synthetic data generation**

- `scikit-learn` needs to be added in the Python packages drop down. This is needed for the synthetic data generation code.
- 4XL Snowpark-optimized warehouse is needed for larger data sizes, for example: 100M. And it takes some time.

Ensure your account has the latest Data Clean Rooms version.

In [ ]:
USE ROLE samooha_app_role;
CALL samooha_by_snowflake_local_db.library.apply_patch();

Create an image repository and grant access to SAMOOHA_APP_ROLE to it.

Capture the repository URL after the execution for the next step.

In [ ]:
USE ROLE ACCOUNTADMIN;

CREATE DATABASE IF NOT EXISTS dcr_spcs;
CREATE SCHEMA IF NOT EXISTS dcr_spcs.repos;
USE SCHEMA dcr_spcs.repos;
CREATE IMAGE REPOSITORY IF NOT EXISTS lal_example;

GRANT USAGE ON DATABASE dcr_spcs TO samooha_app_role; 
grant usage on schema dcr_spcs.repos TO samooha_app_role; 
GRANT READ ON IMAGE REPOSITORY dcr_spcs.repos.lal_example TO samooha_app_role;

SHOW image repositories;
SELECT "repository_url" FROM TABLE(result_scan(last_query_id())) WHERE "name" = 'LAL_EXAMPLE';

Build the docker image and upload it to the repository using the provided _service.zip_. Use the repository URL from the previous step.

If your user does not have multi-factor authentication (MFA) configured, you can use the login command shown below.

However, we recommend you set up a Snowflake CLI connection like in [this tutorial](https://community.snowflake.com/s/article/Authenticating-with-Snowpark-Container-Services-Image-Repository-via-SSO-and-Token-with-Snow-CLI).

Example of commands to build and upload image to the repository using the repository URL from the previous step.

```
docker build --rm --platform linux/amd64 -t <SPCS repository URL>/lal_service_image:latest .

# Works only for users without MFA
# Otherwise use the Snowflake CLI route from the attached above guide
# https://community.snowflake.com/s/article/Authenticating-with-Snowpark-Container-Services-Image-Repository-via-SSO-and-Token-with-Snow-CLI
docker login <SPCS repository domain> -u <snowflake user name>

docker push <SPCS repository URL>/lal_service_image:latest
```

Where:
```
<SPCS repository URL>: org-account.registry.snowflakecomputing.com/dcr_spcs/repos/lal_example
<SPCS repository domain>: org-account.registry.snowflakecomputing.com
```

In [ ]:
-- Confirm the image is available
USE ROLE samooha_app_role;
SHOW IMAGES IN IMAGE REPOSITORY dcr_spcs.repos.lal_example;

Use the code below to generate a synthetic provider dataset. Use a 4XL Snowpark-optimized warehouse for 100M dataset size, or choose a smaller data set size (for example, 10M).

In [ ]:
USE ROLE ACCOUNTADMIN;
CREATE DATABASE IF NOT EXISTS SAMOOHA_SAMPLE_LOOKALIKE_DATABASE;

In [ ]:
import pandas as pd
import numpy as np
from sklearn.datasets import make_classification
from snowflake.snowpark.context import get_active_session

DATABASE_NAME = "SAMOOHA_SAMPLE_LOOKALIKE_DATABASE"
SCHEMA_NAME = "PUBLIC"
TABLE_NAME = "CUSTOMERS"

PROVIDER_SIZE = 100000000

def generate_dcr_datasets(n_features: int = 20, provider_size_count: int = PROVIDER_SIZE):
    X, Y = make_classification(flip_y=0.13, n_samples=provider_size_count, n_features=n_features, n_redundant=0, random_state=1,
                               **{"n_informative": 1, "n_clusters_per_class": 1, "n_classes": 2})
    provider_df = pd.concat([pd.DataFrame(X), pd.DataFrame(Y)], axis=1)
    
    column_name_list = ['FEATURE_' + str(i) for i in range(n_features)] + ['TARGET']
    provider_df.columns = column_name_list
    provider_df['EMAIL'] = provider_df.reset_index()['index'].apply(lambda x:f"email_{x}@fakecorp.com")
    provider_df.drop(columns=['TARGET'], inplace=True)
    return provider_df

provider_df = generate_dcr_datasets()
session = get_active_session()
session.write_pandas(provider_df, TABLE_NAME, database=DATABASE_NAME, schema=SCHEMA_NAME, auto_create_table=True, overwrite=True)
print(f"Generated synthetic provider data: {DATABASE_NAME}.{SCHEMA_NAME}.{TABLE_NAME}")

In [ ]:
USE ROLE ACCOUNTADMIN;
-- Registed the sample database for use with the DCR
CALL samooha_by_snowflake_local_db.provider.register_db('SAMOOHA_SAMPLE_LOOKALIKE_DATABASE');

USE ROLE SAMOOHA_APP_ROLE;
SELECT COUNT(*) FROM SAMOOHA_SAMPLE_LOOKALIKE_DATABASE.PUBLIC.CUSTOMERS;

Create a data clean room, load the provider datasets and set the policies.

In [ ]:
USE ROLE SAMOOHA_APP_ROLE;
SET cleanroom_name = 'SPCS Lookalike Demo';


-- Initialize the cleanroom.
CALL samooha_by_snowflake_local_db.provider.cleanroom_init($cleanroom_name);

-- Link the datasets.
CALL samooha_by_snowflake_local_db.provider.link_datasets(
    $cleanroom_name,
    [ 'SAMOOHA_SAMPLE_LOOKALIKE_DATABASE.PUBLIC.CUSTOMERS' ]
);

-- Set join policies.
CALL samooha_by_snowflake_local_db.provider.set_join_policy(
    $cleanroom_name,
    [ 'SAMOOHA_SAMPLE_LOOKALIKE_DATABASE.PUBLIC.CUSTOMERS:EMAIL' ]
);

Create and load custom templates into the clean room and set corresponding column policies.

Note that SPCS functions will be created under the `service_functions` schema.

In [ ]:
-- Define a template that triggers training using the consumer-supplied seed audience.
{% raw %}
CALL samooha_by_snowflake_local_db.provider.add_custom_sql_template(
    $cleanroom_name,
    'lal_train',
    $$
    select service_functions.train(
              {{ source_table[0] }},
              {{ provider_join_col }},
              {{ my_table[0] }},
              {{ consumer_join_col }},
              {{ dimensions | sqlsafe }},
              {{ filter_clause }}
            ) as train_result;
$$
);
{% endraw %}

-- Define a template that triggers inference on the remaining provider-supplied audience.
{% raw %}
CALL samooha_by_snowflake_local_db.provider.add_custom_sql_template(
    $cleanroom_name,
    'lal_score',
    $$
    select service_functions.score(
          {{ source_table[0] }},
          {{ provider_join_col }},
          {{ my_table[0] }},
          {{ consumer_join_col }},
          {{ dimensions | sqlsafe }}
        ) as score_result;
$$
);
{% endraw %}

-- Define a template that demonstrates batch-based inference.
{% raw %}
CALL samooha_by_snowflake_local_db.provider.add_custom_sql_template(
    $cleanroom_name,
    'lal_score_batches',
    $$
    WITH
    numbered_data AS (
        SELECT
            {{ provider_join_col | sqlsafe }} as id,
            array_construct(identifier({{ dimensions[0] | column_policy }}) {% for feat in dimensions[1:] %} , identifier({{ feat | column_policy }}) {% endfor %}) as features
        FROM identifier({{ source_table[0] }}) as p
        WHERE {{ provider_join_col | sqlsafe }} NOT IN (
                SELECT DISTINCT {{ consumer_join_col | sqlsafe }} FROM identifier({{ my_table[0] }}) as c
        )
    ),
    scored_data AS (
        SELECT service_functions.score_batch(id, features) as score
        FROM numbered_data
    )
    select score:id::STRING as email, score:score::FLOAT as score from scored_data;
$$
);
{% endraw %}

CALL samooha_by_snowflake_local_db.provider.set_column_policy(
    $cleanroom_name,
    [
        'lal_score_batches:SAMOOHA_SAMPLE_LOOKALIKE_DATABASE.PUBLIC.CUSTOMERS:FEATURE_0',
        'lal_score_batches:SAMOOHA_SAMPLE_LOOKALIKE_DATABASE.PUBLIC.CUSTOMERS:FEATURE_1',
        'lal_score_batches:SAMOOHA_SAMPLE_LOOKALIKE_DATABASE.PUBLIC.CUSTOMERS:FEATURE_2',
        'lal_score_batches:SAMOOHA_SAMPLE_LOOKALIKE_DATABASE.PUBLIC.CUSTOMERS:FEATURE_3',
        'lal_score_batches:SAMOOHA_SAMPLE_LOOKALIKE_DATABASE.PUBLIC.CUSTOMERS:FEATURE_4',
        'lal_score_batches:SAMOOHA_SAMPLE_LOOKALIKE_DATABASE.PUBLIC.CUSTOMERS:FEATURE_5',
        'lal_score_batches:SAMOOHA_SAMPLE_LOOKALIKE_DATABASE.PUBLIC.CUSTOMERS:FEATURE_6',
        'lal_score_batches:SAMOOHA_SAMPLE_LOOKALIKE_DATABASE.PUBLIC.CUSTOMERS:FEATURE_7',
        'lal_score_batches:SAMOOHA_SAMPLE_LOOKALIKE_DATABASE.PUBLIC.CUSTOMERS:FEATURE_8',
        'lal_score_batches:SAMOOHA_SAMPLE_LOOKALIKE_DATABASE.PUBLIC.CUSTOMERS:FEATURE_9',
        'lal_score_batches:SAMOOHA_SAMPLE_LOOKALIKE_DATABASE.PUBLIC.CUSTOMERS:FEATURE_10',
        'lal_score_batches:SAMOOHA_SAMPLE_LOOKALIKE_DATABASE.PUBLIC.CUSTOMERS:FEATURE_11',
        'lal_score_batches:SAMOOHA_SAMPLE_LOOKALIKE_DATABASE.PUBLIC.CUSTOMERS:FEATURE_12',
        'lal_score_batches:SAMOOHA_SAMPLE_LOOKALIKE_DATABASE.PUBLIC.CUSTOMERS:FEATURE_13',
        'lal_score_batches:SAMOOHA_SAMPLE_LOOKALIKE_DATABASE.PUBLIC.CUSTOMERS:FEATURE_14',
        'lal_score_batches:SAMOOHA_SAMPLE_LOOKALIKE_DATABASE.PUBLIC.CUSTOMERS:FEATURE_15',
        'lal_score_batches:SAMOOHA_SAMPLE_LOOKALIKE_DATABASE.PUBLIC.CUSTOMERS:FEATURE_16',
        'lal_score_batches:SAMOOHA_SAMPLE_LOOKALIKE_DATABASE.PUBLIC.CUSTOMERS:FEATURE_17',
        'lal_score_batches:SAMOOHA_SAMPLE_LOOKALIKE_DATABASE.PUBLIC.CUSTOMERS:FEATURE_18',
        'lal_score_batches:SAMOOHA_SAMPLE_LOOKALIKE_DATABASE.PUBLIC.CUSTOMERS:FEATURE_19'
]);

Use `provider.load_service_into_cleanroom` API to load the SPCS service.

The API requires two configuration files:
1. SPCS service spec: A YAML file created as part of the service development.
2. Service configuration: A YAML file that describes mapping of service endpoints to functions that will be created inside the clean room.

See working examples of both below.

Note that enabling the `default_service_options.allow_monitoring` option allows the consumers access to the service container logs. If the access is not desired, set this option to FALSE or remove it altogether.

In [ ]:
CALL samooha_by_snowflake_local_db.provider.load_service_into_cleanroom(
    $cleanroom_name,
    $$
    spec:
      containers:
      - name: lal
        image: /dcr_spcs/repos/lal_example/lal_service_image:latest
        env:
          SERVER_PORT: 8000
        readinessProbe:
          port: 8000
          path: /healthcheck
      endpoints:
      - name: lalendpoint
        port: 8000
        public: false
    $$,
    $$
    default_service_options:
      min_instances: 1
      max_instances: 1
      allow_monitoring: true
    
    functions:
      - name: train
        args: PROVIDER_TABLE VARCHAR, PROVIDER_JOIN_COL VARCHAR, CONSUMER_TABLE VARCHAR, CONSUMER_JOIN_COL VARCHAR, DIMENSIONS ARRAY, FILTER VARCHAR
        returns: VARCHAR
        endpoint: lalendpoint
        path: /train
      - name: score
        args: PROVIDER_TABLE VARCHAR, PROVIDER_JOIN_COL VARCHAR, CONSUMER_TABLE VARCHAR, CONSUMER_JOIN_COL VARCHAR, DIMENSIONS ARRAY
        returns: VARCHAR
        endpoint: lalendpoint
        path: /score
      - name: score_batch
        args: ID VARCHAR, FEATURES ARRAY
        returns: VARIANT
        max_batch_rows: 1000
        endpoint: lalendpoint
        path: /scorebatch
$$);

Share the data clean room with your collaborator.

In [ ]:
-- Update the release directive to the patch created by the call above.
-- load_service_into_cleanroom will output the patch number.
CALL samooha_by_snowflake_local_db.provider.set_default_release_directive(
    $cleanroom_name,
    'V1_0',
    '1'
);

CALL samooha_by_snowflake_local_db.provider.add_consumers(
    $cleanroom_name,
    '<CONSUMER_ACCOUNT_LOCATOR>',
    '<CONSUMER_ORG.CONSUMER_ACCOUNT_NAME>'
);

CALL samooha_by_snowflake_local_db.provider.create_or_update_cleanroom_listing($cleanroom_name);

When updating the SPCS service in the clean room, follow the steps below. This includes the following cases:
- The image itself is updated.
- Service spec changed.
- A new function is added.

In [ ]:
USE ROLE SAMOOHA_APP_ROLE;
SET cleanroom_name = 'SPCS Lookalike Demo';

-- Update the manifests, if needed.
-- Or re-run as is to pick up latest image.
CALL samooha_by_snowflake_local_db.provider.load_service_into_cleanroom($cleanroom_name,
    $$
    spec:
      containers:
      - name: lal
        image: /dcr_spcs/repos/lal_example/lal_service_image:latest
        env:
          SERVER_PORT: 8000
        readinessProbe:
          port: 8000
          path: /healthcheck
      endpoints:
      - name: lalendpoint
        port: 8000
        public: false
    $$,
    $$
    default_service_options:
      min_instances: 1
      max_instances: 1
      allow_monitoring: true
    
    functions:
      - name: train
        args: PROVIDER_TABLE VARCHAR, PROVIDER_JOIN_COL VARCHAR, CONSUMER_TABLE VARCHAR, CONSUMER_JOIN_COL VARCHAR, DIMENSIONS ARRAY, FILTER VARCHAR
        returns: VARCHAR
        endpoint: lalendpoint
        path: /train
      - name: score
        args: PROVIDER_TABLE VARCHAR, PROVIDER_JOIN_COL VARCHAR, CONSUMER_TABLE VARCHAR, CONSUMER_JOIN_COL VARCHAR, DIMENSIONS ARRAY
        returns: VARCHAR
        endpoint: lalendpoint
        path: /score
      - name: score_batch
        args: ID VARCHAR, FEATURES ARRAY
        returns: VARIANT
        max_batch_rows: 1000
        endpoint: lalendpoint
        path: /scorebatch
$$);

In [ ]:
-- Update the release directive to the patch created by the call above.
-- load_service_into_cleanroom will output the patch number.
CALL samooha_by_snowflake_local_db.provider.set_default_release_directive(
    $cleanroom_name,
    'V1_0',
    '2'
);